In [1]:
#Imports
from comet_ml import Experiment
experiment = Experiment(api_key="XXXXXXXXXXX", parse_args=False, project_name='XXXXXXXX')

COMET INFO: old comet version (1.0.44) detected. current: 1.0.51 please update your comet lib with command: `pip install --no-cache-dir --upgrade comet_ml`
COMET WARNING: Failing to collect the installed os packages
COMET INFO: Experiment is live on comet.ml https://www.comet.ml/yikeqicn/segnet/19b73fadff324232a8e6478bdb272271



In [2]:
from os.path import join, basename, dirname
import tensorflow as tf
import shutil
import os
import sys
import argparse

import cv2
import numpy as np
import os
import time

from torch.utils.data import DataLoader, ConcatDataset, random_split#, SequentialSampler #yike: add SequentialSampler
import torch
import torchvision
import torchvision.transforms as transforms
from datasets import ArtPrint, ArtPrintNoIntsect,ArtPrintNoIntsectBinary,ArtPrintNoIntsectLBW
from Model_Unet_github import *

home = os.environ['HOME']

In [3]:
#General Settings
parser = argparse.ArgumentParser()

# system basics
parser.add_argument("-name", default='segnet_unet_lbw_bpr_siameydg_100_epoches', type=str, help="name of the log") #debug model_intersect # segnet_no_intersect_1conv_64_channels_30epoch_unet_github
parser.add_argument("-gpu", default='2', type=str, help="gpu numbers")

parser.add_argument("-train", default=True, help="train the NN", action="store_true")

parser.add_argument("-transfer",default=False, help="test the NN", action="store_true")

parser.add_argument("-test",default=False, help="test the NN", action="store_true")

# image and logistic parameters 
parser.add_argument("-image_h", default=32, type=int, help='image height') #('image_h', "360", """ image height """) 32
parser.add_argument("-image_w", default=128, type=int, help='image width')#('image_w', "480", """ image width """)128
#parser.add_argument("-image_h", default=360, type=int, help='image height') 
#parser.add_argument("-image_w", default=480, type=int, help='image width')

parser.add_argument("-image_c", default=1, type=int, help='image channel')#('image_c', "3", """ image channel (RGB) """)
parser.add_argument("-num_class", default=2, type=int, help='total class number')

# training hyperparam
parser.add_argument("-batch_size", default=10, type=int, help='batch_size')
parser.add_argument("-lrInit", default=1e-3, type=int, help='initial lr')
parser.add_argument("-lrDrop1", default=10, type=int, help='step to drop lr by 10 first time') # not sure
parser.add_argument("-lrDrop2", default=1000, type=int, help='step to drop lr by 10 sexond time') # not sure
parser.add_argument('-max_epoch',default=100, type=int,help='max epoch numbers')



# file paths
parser.add_argument('-ckpt_root', default="/root/ckpt", type=str,help= "dir to store ckpt") # log_dir !!!!!
parser.add_argument('-data_root', default="/root/datasets", type=str, help=" root to any data folder ")
parser.add_argument('-urlTranferFrom', default="", type=str, help=" archived model url ")


#args = parser.parse_args()
args = parser.parse_known_args()[0]

name = args.name

experiment.set_name(name)
experiment.log_parameters(vars(args))

os.environ['CUDA_VISIBLE_DEVICES'] = args.gpu

ckptroot = args.ckpt_root
args.ckptpath = join(ckptroot, name)
if args.name=='debug': shutil.rmtree(args.ckptpath, ignore_errors=True)
os.makedirs(args.ckptpath, exist_ok=True)


In [4]:
def checkArgs():
    if args.test:
        print('The model is set to Testing')
        print("Check point file: %s"%args.ckptpath)
        #print("CamVid testing dir: %s"%FLAGS.test_dir)
    elif args.transfer:
        print('The model is set to transfer learn from ckpt')
        print("Check point file: %s"%args.ckptpath)
        #print("CamVid Image dir: %s"%FLAGS.image_dir)
        #print("CamVid Val dir: %s"%FLAGS.val_dir)
    else:
        print('The model is set to Training')
        print("Max training Iteration: %d"%args.max_epoch)
        print("Initial lr: %f"%args.lrInit)
        print("First Drop Steps: %i"%args.lrDrop1)
        print("Second Drop Steps: %i"%args.lrDrop2)
        print("Data root: %s"%args.data_root)
        print("Check point file: %s"%args.ckptpath)
        #print("CamVid Val dir: %s"%FLAGS.val_dir)

    print("Batch Size: %d"%args.batch_size)

In [5]:
#main function
def main():    
    checkArgs()
    if args.train:
        transform_train = transforms.Compose([
          transforms.Lambda(lambda img: cv2.resize(img, (args.image_w,args.image_h), interpolation=cv2.INTER_CUBIC)),
          transforms.Lambda(lambda img: np.expand_dims(img,3) ),
          #transforms.Lambda(lambda img: add_artifacts(img,args)),
          #transforms.Lambda(lambda img: cv2.transpose(img))
        ])
        #arprint=ArtPrint(args.data_root, transform=transform_train)
        arprint=ArtPrintNoIntsectLBW(args.data_root, transform=transform_train)
        concat=arprint
        print(len(arprint))
        idxTrain = int( len(arprint)*0.9)
        trainset, testset = random_split(concat, [idxTrain, len(concat)-idxTrain])
        trainloader = DataLoader(trainset, batch_size=args.batch_size, shuffle=True, drop_last=True,num_workers=4)
        testloader = DataLoader(testset, batch_size=args.batch_size, shuffle=False, drop_last=False,num_workers=2)
        
        #weight gen
        pos_perc=sum(map(lambda x: np.sum(cv2.imread(x[1],cv2.IMREAD_GRAYSCALE)),trainset.dataset.samples))/(args.image_h*args.image_w*len(trainset.dataset.samples))
        neg_perc=1-pos_perc
        weight=np.array([pos_perc,neg_perc]) # just reverse
        print(weight)
        model=Model(args, experiment, loss_weight=weight, mustRestore=False)
        model.training(loader=trainloader, validateloader=testloader)
        
    else:
        pass # for now, leave it pass 
    

In [6]:
main()

The model is set to Training
Max training Iteration: 100
Initial lr: 0.001000
First Drop Steps: 10
Second Drop Steps: 1000
Data root: /root/datasets
Check point file: /root/ckpt/segnet_unet_lbw_bpr_siameydg_100_epoches
Batch Size: 10
284246
[0.09025098 0.90974902]
Instructions for updating:
Colocations handled automatically by placer.
GGG
[None, 32, 128, 1]
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


Instructions for updating:
Deprecated in favor of operator or tf.math.divide.


Instructions for updating:
Deprecated in favor of operator or tf.math.divide.


0 conv1: (?, ?, ?, 32)
0 conv2: (?, ?, ?, 32)
1 conv1: (?, ?, ?, 64)
1 conv2: (?, ?, ?, 64)
2 conv1: (?, ?, ?, 128)
2 conv2: (?, ?, ?, 128)
1 h_deconv: (?, ?, ?, 64)
1 h_deconv_concat: (?, ?, ?, ?)
1 h_conv1_post_deconv: (?, ?, ?, 64)
1 h_conv2_post_deconv: (?, ?, ?, 64)
0 h_deconv: (?, ?, ?, 32)
0 h_deconv_concat: (?, ?, ?, ?)
0 h_conv1_post_deconv: (?, ?, ?, 32)
0 h_conv2_post_deconv: (?, ?, ?, 32)
0 outmap: (?, ?, ?, 2)
(?, ?, ?, 2)
loss: ()
INFO:tensorflow:Summary name loss/cross_entropy (raw) is illegal; using loss/cross_entropy__raw_ instead.


...

TRAIN: Batch: 0.574622781643343 Loss: 0.014377931
accuracy = 0.963565
mean IU  = 0.848437
    class # 0 capture rate = 0.961242 
    class # 1 capture rate = 0.983572 
TRAIN: Batch: 0.5785317801579235 Loss: 0.015063563
accuracy = 0.948505
mean IU  = 0.796590
    class # 0 capture rate = 0.944332 
    class # 1 capture rate = 0.987396 
TRAIN: Batch: 0.5824407786725041 Loss: 0.011392775
accuracy = 0.971498
mean IU  = 0.846653
    class # 0 capture rate = 0.971064 
    class # 1 capture rate = 0.976722 
TRAIN: Batch: 0.5863497771870847 Loss: 0.01907242
accuracy = 0.937906
mean IU  = 0.781276
    class # 0 capture rate = 0.933582 
    class # 1 capture rate = 0.973027 
TRAIN: Batch: 0.5902587757016652 Loss: 0.012784612
accuracy = 0.961753
mean IU  = 0.810931
    class # 0 capture rate = 0.960540 
    class # 1 capture rate = 0.976258 
TRAIN: Batch: 0.5941677742162458 Loss: 0.016928226
accuracy = 0.946436
mean IU  = 0.777213
    class # 0 capture rate = 0.943108 
    class # 1 capture rate 

TRAIN: Batch: 0.7661637088577906 Loss: 0.013364661
accuracy = 0.960877
mean IU  = 0.819314
    class # 0 capture rate = 0.959223 
    class # 1 capture rate = 0.978571 
TRAIN: Batch: 0.7700727073723712 Loss: 0.016759377
accuracy = 0.952753
mean IU  = 0.791807
    class # 0 capture rate = 0.951026 
    class # 1 capture rate = 0.971429 
TRAIN: Batch: 0.7739817058869518 Loss: 0.016247448
accuracy = 0.951352
mean IU  = 0.776753
    class # 0 capture rate = 0.949546 
    class # 1 capture rate = 0.973016 
TRAIN: Batch: 0.7778907044015323 Loss: 0.01618905
accuracy = 0.951975
mean IU  = 0.796660
    class # 0 capture rate = 0.949779 
    class # 1 capture rate = 0.974199 
TRAIN: Batch: 0.7817997029161129 Loss: 0.01425882
accuracy = 0.959295
mean IU  = 0.802952
    class # 0 capture rate = 0.957409 
    class # 1 capture rate = 0.981916 
TRAIN: Batch: 0.7857087014306935 Loss: 0.012875482
accuracy = 0.959041
mean IU  = 0.806166
    class # 0 capture rate = 0.956978 
    class # 1 capture rate 

TRAIN: Batch: 0.9577046360722383 Loss: 0.016372304
accuracy = 0.954444
mean IU  = 0.816262
    class # 0 capture rate = 0.952090 
    class # 1 capture rate = 0.975485 
TRAIN: Batch: 0.9616136345868188 Loss: 0.01957666
accuracy = 0.951934
mean IU  = 0.797421
    class # 0 capture rate = 0.950665 
    class # 1 capture rate = 0.964524 
TRAIN: Batch: 0.9655226331013994 Loss: 0.011054615
accuracy = 0.968008
mean IU  = 0.820095
    class # 0 capture rate = 0.967610 
    class # 1 capture rate = 0.973458 
TRAIN: Batch: 0.96943163161598 Loss: 0.011290627
accuracy = 0.965190
mean IU  = 0.829263
    class # 0 capture rate = 0.963475 
    class # 1 capture rate = 0.984634 
TRAIN: Batch: 0.9733406301305606 Loss: 0.014487562
accuracy = 0.958527
mean IU  = 0.835007
    class # 0 capture rate = 0.956179 
    class # 1 capture rate = 0.978102 
TRAIN: Batch: 0.9772496286451411 Loss: 0.013774427
accuracy = 0.961574
mean IU  = 0.802750
    class # 0 capture rate = 0.960710 
    class # 1 capture rate =

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:7: DeprecationWarning: Both axis > a.ndim and axis < -a.ndim - 1 are deprecated and will raise an AxisError in the future.
  import sys
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:7: DeprecationWarning: Both axis > a.ndim and axis < -a.ndim - 1 are deprecated and will raise an AxisError in the future.
  import sys


VALID: Total accuracy: 95.798096%. Class 0 capture: 95.621949%. Class 1 capture: 97.584331%
Character error rate improved, save model
Done with training at epoch 100 sigoptObservation=0.9579809611095589
